# Le projet : Decision science  « Une chaussure à son pied »

**Contexte**:  

Vous êtes sollicités par un client: Jean Mimi Chaussure. Il souhaite ouvrir une boutique de chaussures pour homme dans le centre de Bordeaux. Il n'en est qu'au début de son étude de marché et souhaite que vous l'aidiez dans sa prise de décision.

**Consigne** :   

*Première étape* : 
- Le format des données (exploitables en l'état ou nécessite un traitement,...)
- La taille du dataset (le poids des fichiers, le nombre d'observations, le nombre de features,...)
- Puis après on fait un état des lieux (Nombre de valeurs inexploitables (replicat, nan,...), colinéarité des features, autocorrelation,....)
Bref on corrige pas forcément mais on regarde ce que l'on a et si ce sera suffisant pour tendre vers le résultat attendu.
    

**Rendu attendu de cette première étape** : 
- Présentation de la phase exploratoire (notebook présentation imposée)
- Trello avec la structure adaptée (les listes) et les tâches
- Planning avec les sprints (contenu des livrables et leur deadlines)

# Le besoin client

**Besoins client**:

- Quelle est la meilleure cible (les jeunes, les sportifs, un mixte…)
- Quels sont les meilleurs produits ? np : les produits les plus vendus ?
- Quel est le volume de stock pour être le plus rentables ?
- Manque t’il des infos pour investiguer ?
-------------------------------------------------------------------------------------------

Notes : 
- Ce dataset n'est pas optimal pour cibler la clientèle désirée. En revanche, il est intéressant pour définir le prix de vente d'une marque et connaître les marques qui ont appliqué les prix les plus élevés.
- Top 30 des meilleures ventes des modèles (code EAN/UPC) -> 1 modèle d'une marque
- Top 30 des meilleures ventes selon la marque
- Soldes : déterminer si certaines marques se vendent plus lorsqu'elles sont en solde. Des marques se vendent peut-être mieux en solde alors que cela ne change pas pour certaines ? 
- Stock : on n'a pas les stocks initiaux => données que sur les chaussures vendues. 
- Analyse du prix des marques : 
- Fixer les prix par modèle et marque : Analyse du prix des marques (prix moyen, max et min, prix les plus étendus) + propositions en fonction de la cible client (population et lieu d'installation de la boutique) + distribution des prix (histo + qqplot + loi normale ou non ? + nécessité de logarithmer ?)

----------------------------------------------------------------------------------------

Piste d'amélioration : 
- récupérer le prix d'achat afin de calculer la marge


**Questions à poser au client** : 
- A-t-il défini sa cible de départ (étude de marché faite) ? 
    Si oui : Où souhaite-t-il s'installer ? Quelle est la tranche d'âge et quel prix moyen est prêt à dépenser un client ?
    Si non : inviter le client à recueillir ces infos ou tâche en plus à facturer (analyse de marché)

# Nos premières observations

**Description des variables retenues**: 

- *descriptions* : peut-être ne garder que la provenance  
- *features* = on a toutes les informations nécessaires sous forme d'une liste de dictionnaire
- *prices_amountmax / prices_amountmin* = vérifier si toutes les valeurs sont identiques. Si oui, supprimer la colonne max / si non, faire la moyenne. /!\ présence de
- *colors* : couleurs disponibles
- *features* : value = color de la chaussure achetée

**Premières observations** :
- nettoyage important des données (d'après Kaggle, la catégorisation des accessoires serait une erreur de sourcing des données) 

**Phase exploratoire**
- data.shape (de quelles données parle-t-on et d'où viennent les données) + poids des fichiers
- data.isnull (avec le graphique data.isnull -> retrouver code projet turbine) + suppression
- analyse une par une des features qui nous intéressent (justifier) + data.dtypes (convertir les données en numérique)
- Petit nettoyage préablable : supprimer les lignes qui ne concernent pas les chaussures hommes + suppression features non intéressantes => distribution des variables les plus importantes (prix) + matrice de correlation avec les features sélectionnées + multicolinéarité

**Définition des tâches**
- définir les sprints ? Attendre d'avoir la réponse des questions à poser au client ou proposer 2 types de sprint ?

- trello + planning
- devis virtuel ?

- data cleaning : lister les opérations à faire dans le détail qui vont chiffrer le devis

In [1]:
import pandas as pd
import numpy as np
import pandas_profiling
import json

In [5]:
data = pd.read_csv('train.csv')

C:\Users\Gwen\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3418: DtypeWarning: Columns (39,45) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [18]:
data.head()

id asins                brand  \
0  AVpfHrJ6ilAPnD_xVXOI   NaN                Josmo   
1  AVpfHrJ6ilAPnD_xVXOI   NaN                Josmo   
2  AVpfHsWP1cnluZ0-eVZ7   NaN  SERVUS BY HONEYWELL   
3  AVpfHsWP1cnluZ0-eVZ7   NaN  SERVUS BY HONEYWELL   
4  AVpfHsWP1cnluZ0-eVZ7   NaN  SERVUS BY HONEYWELL   

                                   categories colors  count  \
0  Clothing,Shoes,Men's Shoes,All Men's Shoes    NaN    NaN   
1  Clothing,Shoes,Men's Shoes,All Men's Shoes    NaN    NaN   
2  All Men's Shoes,Shoes,Men's Shoes,Clothing    NaN    NaN   
3  All Men's Shoes,Shoes,Men's Shoes,Clothing    NaN    NaN   
4  All Men's Shoes,Shoes,Men's Shoes,Clothing    NaN    NaN   

              dateadded           dateupdated  \
0  2016-11-07T00:45:12Z  2016-11-07T00:45:12Z   
1  2016-11-07T00:45:12Z  2016-11-07T00:45:12Z   
2  2016-06-14T04:29:57Z  2016-07-09T20:26:48Z   
3  2016-06-14T04:29:57Z  2016-07-09T20:26:48Z   
4  2016-06-14T04:29:57Z  2016-07-09T20:26:48Z   

                                        descriptions dimension  ...  \
0  [{"dateSeen":["2016-11-07T00:45:12Z"],"sourceU...       NaN  ...   
1  [{"dateSeen":["2016-11-07T00:45:12Z"],"sourceU...       NaN  ...   
2  [{"dateSeen":["2016-07-09T20:26:48Z"],"sourceU...       NaN  ...   
3  [{"dateSeen":["2016-07-09T20:26:48Z"],"sourceU...       NaN  ...   
4  [{"dateSeen":["2016-07-09T20:26:48Z"],"sourceU...       NaN  ...   

   prices_warranty quantities  reviews sizes  skus  \
0              NaN        NaN      NaN   NaN   NaN   
1              NaN        NaN      NaN   NaN   NaN   
2              NaN        NaN      NaN   NaN   NaN   
3              NaN        NaN      NaN   NaN   NaN   
4              NaN        NaN      NaN   NaN   NaN   

                                          sourceurls           upc  vin  \
0  https://www.walmart.com/ip/Josmo-8190-Plain-In...  699302044036  NaN   
1  https://www.walmart.com/ip/Josmo-8190-Plain-In...  699302044036  NaN   
2  http://www.walmart.com/ip/Studs-Shoe-Large-Pr-...           NaN  NaN   
3  http://www.walmart.com/ip/Studs-Shoe-Large-Pr-...           NaN  NaN   
4  http://www.walmart.com/ip/Studs-Shoe-Large-Pr-...           NaN  NaN   

  websiteids weight  
0        NaN    NaN  
1        NaN    NaN  
2        NaN    NaN  
3        NaN    NaN  
4        NaN    NaN  

[5 rows x 48 columns]

In [16]:
data.isnull().sum()

id                         0
asins                  16816
brand                    258
categories                 0
colors                  8339
count                  19387
dateadded                  0
dateupdated                0
descriptions            9483
dimension              16396
ean                     9388
features                5390
flavors                19387
imageurls               1045
isbn                   19387
keys                       0
manufacturer           12688
manufacturernumber      4240
merchants               5347
name                       0
prices_amountmin          10
prices_amountmax           0
prices_availability    19190
prices_color           18629
prices_condition        6766
prices_count           19316
prices_currency           76
prices_dateadded          15
prices_dateseen           25
prices_flavor          19311
prices_issale             66
prices_merchant         5544
prices_offer           13296
prices_returnpolicy    18369
prices_shippin

In [11]:
pandas_profiling.ProfileReport(data)

In [17]:
# drop colonnes avec plus de 80% de nulles

df = [col for col in data.columns if data[col].isna().sum() >= 0.5*data.shape[0]]
df

['asins',
 'count',
 'dimension',
 'flavors',
 'isbn',
 'manufacturer',
 'prices_availability',
 'prices_color',
 'prices_count',
 'prices_flavor',
 'prices_offer',
 'prices_returnpolicy',
 'prices_shipping',
 'prices_size',
 'prices_source',
 'prices_warranty',
 'quantities',
 'reviews',
 'sizes',
 'skus',
 'vin',
 'websiteids',
 'weight']